<a href="https://colab.research.google.com/github/vanderbilt-data-science/lo-achievement/blob/update_UI_with_prompts/gradio_application.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Gradio Interface Draft

The goal of this notebook is to show a draft of a comprehensive Gradio interface though which students can interface with an LLM and self-study.

## Libraries

In [1]:
# install libraries here
# -q flag for "quiet" install
!pip install -q langchain
!pip install -q openai
!pip install -q gradio
!pip install -q unstructured
!pip install -q chromadb
!pip install -q tiktoken
!pip install Pillow==9.0.0
!pip install -q reportlab

DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 23.3 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063
DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 23.3 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063
DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 23.3 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at 

In [2]:
# import libraries here
import os
import time
from getpass import getpass

from langchain.docstore.document import Document
from langchain.prompts import PromptTemplate
from langchain.document_loaders import TextLoader
from langchain.indexes import VectorstoreIndexCreator
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings import OpenAIEmbeddings

from langchain.document_loaders.unstructured import UnstructuredFileLoader
from langchain.vectorstores import Chroma
from langchain.chains import RetrievalQA, RetrievalQAWithSourcesChain
from langchain.chains.qa_with_sources import load_qa_with_sources_chain
#from langchain.chains import ConversationalRetrievalChain

from langchain.llms import OpenAI
from langchain.chat_models import ChatOpenAI

import gradio as gr
from sqlalchemy import TEXT # TODO Why is sqlalchemy imported

import pprint

import json
from google.colab import files
from reportlab.pdfgen.canvas import Canvas

ModuleNotFoundError: No module named 'langchain'

# Export requirements.txt (if needed)

In [4]:
!pip freeze > requirements.txt

## API Keys

Use these cells to load the API keys required for this notebook. The below code cell uses the `getpass` library.

In [3]:
openai_api_key = getpass()
os.environ["OPENAI_API_KEY"] = openai_api_key

··········


In [4]:
llm = ChatOpenAI(model_name = 'gpt-3.5-turbo-16k')
# TODO OpenAI() or ChatOpenAI()?

# Interface

In [5]:
global db # Document-storing object (vector store / index)
global qa # Question-answer object; retrieves from `db`
global srcs # List of source documents fragments referenced by vector store
num_sources = 100 # Maximum number of source documents which can be shown

srcs = []
# See https://github.com/hwchase17/langchain/discussions/3786 for discussion
# of which splitter to use
text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=0)

In [6]:
### Source Display ###

def format_source_reference(document, index):
  """Return a HTML element which contains the `document` info and can be
  referenced by the `index`."""
  if 'source' in document.metadata:
    source_filepath, source_name = os.path.split(document.metadata['source'])
  else:
    source_name = "text box"
  return  f"<p id='source{index}'>[{index+1}] <em>{source_name}</em><br>...{document.page_content}...</p>"

def format_source_citation(index):
  """Return a Markdown element which references the element with the given
  `index`."""
  return f"[{index+1}](#source{index})"

def update_source_list(added_sources):
  """Add any new sources to the list `srcs`; return a list of integers
  containing the index references for each of the given sources in `sources`."""
  source_indices = []
  for source in added_sources:
    if source not in srcs: srcs.append(source)
    source_indices.append(srcs.index(source))
  return source_indices

def get_source_display_updates(sources=srcs):
  """Dynamically update the output for the given list of components to show
  the items as contained within the documents in `sources`.
  See https://github.com/gradio-app/gradio/issues/2066 for what I'm copying."""
  # TODO Currently displays the first 100 sources only, which could be an issue
  # TODO Display an alert when the source display is being cut off (over 100
  # sources are stored)
  update_list = []
  for i in range(num_sources):
    if i < len(sources):
      source_text = format_source_reference(sources[i], i)
      update_list.append(gr.update(visible=True, value=source_text))
    else:
      update_list.append(gr.update(visible=False))
  return update_list

In [7]:
def embed_key(openai_api_key):
  os.environ["OPENAI_API_KEY"] = openai_api_key

### Helper Functions ###

def create_vector_store_from_document_segments(document_segments):
  """Updates the global `db` and `qa` variables to contain the given sections
  of text (generated from the create_vector_store_from_file and
  create_vector_store_from_text_input functions)."""
  global db, qa

  # TODO: Add useful metadata that indicates from *where* in the document
  # the segment is pulled (ideally, show what page it's from, if possible)
  # This requires changing how the info is displayed in the UI, but it
  # shouldn't be a big change
  embeddings = OpenAIEmbeddings()
  db = Chroma.from_documents(document_segments, embeddings)
  retriever = db.as_retriever()

  qa = RetrievalQAWithSourcesChain.from_chain_type(llm=llm,
                                  chain_type="stuff",
                                  retriever=retriever,
                                  return_source_documents=True)

def get_document_segments_from_files(files):
  """Returns a list of document segments taken from all of the files in the
  given list."""
  # TODO Modify the metadata for each document to specify the location; see
  # colab.research.google.com/drive/142CCh-Mh1AdodIGD7PyL86slFLOcVVeI
  all_document_segments = []
  for file in files:
    loader = UnstructuredFileLoader(file.name)
    documents = loader.load()
    document_segments = text_splitter.split_documents(documents)
    all_document_segments.extend(document_segments)
  return all_document_segments

def get_document_segments_from_text(text):
  """Returns a list of document segments taken from the text."""
  return [Document(page_content=page, metadata={"source":"text box"})
                      for page in text_splitter.split_text(text)]

def create_vector_store_from_file(file):
  """Updates the global `db` and `qa` variables to contain the given file."""
  # TODO change the code to allow input of multiple files (see previous
  # implementation of this in some other notebook I made)
  loader = UnstructuredFileLoader(file.name)
  documents = loader.load()
  document_segments = text_splitter.split_documents(documents)
  create_vector_store_from_document_segments(document_segments)

def create_vector_store_from_files(files):
  """Updates the global `db` and `qa` variables to contain the given files."""
  document_segments = get_document_segments_from_files(files)
  create_vector_store_from_document_segments(document_segments)

def create_vector_store_from_text(text):
  """Updates the global `db` and `qa` variables to contain the given string."""
  document_segments = get_document_segments_from_text(text)
  create_vector_store_from_document_segments(document_segments)

# TODO I keep on getting the following error (or something similar):
# openai.error.InvalidRequestError: This model's maximum context length is 4097
# tokens, however you requested 4333 tokens (4077 in your prompt; 256 for the
# completion). Please reduce your prompt; or completion length.

def construct_prompt(prompt, learning_objective):
  # TODO Use prompt templates instead of just adding the strings together
  return prompt + " " + learning_objective

def generate_response(prompt, learning_objective=''):
  """Get the LLM response to the given prompt with the given learning objective,
  referencing the global `qa` variable."""
  global db, qa
  qa_prompt = construct_prompt(prompt, learning_objective)
  result = qa({"question": qa_prompt})
  return result["answer"], result["source_documents"]

def generate_response_with_document_update(prompt, learning_objective=''):
  """Get the LLM response to the given prompt with the given learning objective,
  referencing the global `qa` variable, and also return the document updates."""
  answer, sources = generate_response(prompt, learning_objective)
  update_source_list(sources)
  return [answer, *get_source_display_updates()]

In [8]:
### Source Display ###

def format_source_reference(document, index):
  """Return a HTML element which contains the `document` info and can be
  referenced by the `index`."""
  source_filepath, source_filename = os.path.split(document.metadata['source'])
  return  f"<p id='source{index}'>[{index+1}] <em>{source_filename}</em><br>...{document.page_content}...</p>"

def format_source_citation(index):
  """Return a Markdown element which references the element with the given
  `index`."""
  return f"[{index+1}](#source{index})"

def update_source_list(added_sources):
  """Add any new sources to the list `srcs`; return a list of integers
  containing the index references for each of the given sources in `sources`."""
  source_indices = []
  for source in added_sources:
    if source not in srcs: srcs.append(source)
    source_indices.append(srcs.index(source))
  return source_indices

def get_source_display_updates(sources=srcs):
  """Dynamically update the output for the given list of components to show
  the items as contained within the documents in `sources`.
  See https://github.com/gradio-app/gradio/issues/2066 for what I'm copying."""
  # TODO Currently displays the first 100 sources only, which could be an issue
  # TODO Display an alert when the source display is being cut off (over 100
  # sources are stored)
  update_list = []
  for i in range(num_sources):
    if i < len(sources):
      source_text = format_source_reference(sources[i], i)
      update_list.append(gr.update(visible=True, value=source_text))
    else:
      update_list.append(gr.update(visible=False))
  return update_list

In [21]:
### Gradio Called Functions ###

def prompt_select(selection, number, length):
  if selection == "Random":
    prompt = f"Please design a {number} question quiz based on the context provided and the inputted learning objectives (if applicable). The types of questions should be randomized (including multiple choice, short answer, true/false, short answer, etc.).  Provide one question at a time, and wait for my response before providing me with feedback. Again, while the quiz may ask for multiple questions, you should only provide 1 question in you initial response. Do not include the answer in your response. If I get an answer wrong, provide me with an explanation of why it was incorrect, and then give me additional chances to respond until I get the correct choice. Explain why the correct choice is right."
  elif selection == "Fill in the Blank":
    prompt = f"Create a {number} question fill in the blank quiz refrencing the context provided. The quiz should reflect the learning objectives (if inputted). The 'blank' part of the question should appear as '________'. The answers should reflect what word(s) should go in the blank an accurate statement. An example is the follow: 'The author of the article is ______.' The question should be a statement. Provide one question at a time, and wait for my response before providing me with feedback. Again, while the quiz may ask for multiple questions, you should only provide ONE question in you initial response. Do not include the answer in your response. If I get an answer wrong, provide me with an explanation of why it was incorrect,and then give me additional chances to respond until I get the correct choice. Explain why the correct choice is right."
  elif selection == "Short Answer":
    prompt = f"Please design a {number} question quiz about which reflects the learning objectives (if inputted).  The questions should be short answer. Expect the correct answers to be {length} sentences long. Provide one question at a time, and wait for my response before providing me with feedback. Again, while the quiz may ask for multiple questions, you should only provide ONE question in you initial response. Do not include the answer in your response. If I get an answer wrong, provide me with an explanation of why it was incorrect, and then give me additional chances to respond until I get the correct choice. Explain why the correct answer is right."
  else:
    prompt = f"Please design a {number} question {selection.lower()} quiz based on the context provided and the inputted learning objectives (if applicable). Provide one question at a time, and wait for my response before providing me with feedback. Again, while the quiz may ask for multiple questions, you should only provide 1 question in you initial response. Do not include the answer in your response. If I get an answer wrong, provide me with an explanation of why it was incorrect, and then give me additional chances to respond until I get the correct choice. Explain why the correct choice is right."
  return prompt

'''
def generate_response_with_document(file_input, text_input,
                                    prompt, learning_objective):
  """Determine which type of document input is given and call the corresponding
  function to generate and return a response, along with the sources."""
  if file_input:
    return generate_response_from_files(file_input, prompt, learning_objective)
  elif text_input:
    return generate_response_from_text(text_input, prompt, learning_objective)
  else: # No document input
    # TODO add a UI indicator to the student if they forgot to provide document
    raise Exception("No source text or file given")
'''
pass

In [10]:
### Chatbot Functions ###

def user(user_message, history):
  """Display user message and update chat history to include it.
  Also disables user text input until bot is finished (call to reenable_chat())
  See https://gradio.app/creating-a-chatbot/"""
  return gr.update(value="", interactive=True), history + [[user_message, None]]

def get_chatbot_response(history):
  """Given the history as a list of tuples of strings, output the new history
  response (referencing the document via vector store `qa`), along with the
  currently referenced sources."""

  # TODO Disable input when the user has not added a document for context
  # Right now, if you try to use this before pressing one of the other
  # generator buttons, it breaks!
  if not qa: raise Exception("No source text or file given")
  history = history or [] # Account for issue if history is empty
  # Turn nested list into string:
  # [["Hello HAL", "Hi Dave"], ["Open the pod bay doors", "No."]] ->
  # "Hello HAL\nHi Dave\nOpen the pod bay doors\nNo."
  # TODO: This conversion doesn't distinguish between the input of the user
  # and the output from the model... I could add tags for each section, e.g.
  # "USER:Hello HAL\nBOT:Hi Dave\nUSER:Open the pod bay doors\nBOT:No."
  # But that uses up extra tokens... we need to figure out if that's worth it
  history_flat = [message for exchange in history
               for message in exchange if message]
  history_string = '\n'.join(history_flat)
  response = generate_response(history_string)
  return response

def bot(history, use_model=True, character_crawl=False):
  """Get model response based on chat history (including user input).
  If use_model is False, then return a placeholder value.
  If character_crawl, then show each character in the output one at a time.
  See https://gradio.app/creating-a-chatbot/"""

  answer, sources = get_chatbot_response(history) if use_model \
      else ("This is a placeholder message.", [])

  # Add the link to the sources
  #bot_message = f"{answer}\n[Sources](#sources)"
  source_indices = update_source_list(sources)
  source_citations = " ".join(format_source_citation(source_index)
                      for source_index in source_indices)
  bot_message = answer + "\nSources: " + source_citations

  """
  if character_crawl:
    # Display generated response, one character at a time
    # TODO doesn't work if the history is empty (no messages)
    # However, get_chatbot_response() should always output something, so it's fine
    history[-1][1] = ""
    for character in bot_message:
        history[-1][1] += character
        # TODO Remove timeout
        time.sleep(0.01)
        yield history
  else:
    history[-1][1] = bot_message
    yield history
  """
  history[-1][1] = bot_message
  yield [history, *get_source_display_updates()]

def reenable_chat():
  """Called after user() disables chat and bot provides response, meaning
  the user is now free to add follow-up questions / comments to chatbot."""
  gr.update(interactive=True)

In [11]:
# Downloadable formats

def save_chatbot_dialogue(chatbot, filename='chatbot_dialogue.json'):
  with open(filename, 'w') as file:
    json.dump(chatbot, file)
  files.download(filename)

def list_to_str(chatbot):
  total_interaction = ""
  for line in chatbot:
    if line[0]:
      user_message = "User: " + line[0] + "\n"
      total_interaction += user_message
    if line[1]:
      chat_message = "Bot: " + line[1] + "\n"
      total_interaction += chat_message
  return total_interaction

from textwrap import wrap
def save_chatbot_dialogue_pdf(chatbot, filename="chatbot_dialogue.pdf"):
  chatbot = list_to_str(chatbot)
  canvas = Canvas(filename)
  t = canvas.beginText()
  t.setFont('Helvetica', 12)
  t.setCharSpace(2)
  t.setTextOrigin(50, 750)
  t.textLines(chatbot)
  canvas.drawText(t)
  canvas.save()
  files.download(filename)

def save_as_txt(chatbot, filename = 'chat_dialogue.txt'):
  chatbot = list_to_str(chatbot)
  with open(filename, 'w') as file:
    file.write(chatbot)
  files.download(filename)

def save_as_csv(chatbot, filename = 'chat_dialogue.csv'):
  chatbot = list_to_str(chatbot)
  with open(filename, 'w') as file:
    file.write(chatbot)
  files.download(filename)

In [12]:
# Function to save prompts (premade or custom) and return in the user input box in the chatbot

saved_text = ""
def save_text(text):
    global saved_text
    saved_text = text

def return_text():
    # Return the saved text
    return saved_text

In [22]:
# See https://gradio.app/custom-CSS-and-JS/
css="""
#sources-container {
  overflow: scroll !important; /* Needs to override default formatting */
  /*max-height: 20em; */ /* Arbitrary value */
}
#sources-container > div { padding-bottom: 1em !important; /* Arbitrary value */ }
.short-height > * > * { min-height: 0 !important; }
.translucent { opacity: 0.5; }
.textbox_label { padding-bottom: .5em; }
"""
#srcs = [] # Reset sources (db and qa are kept the same for ease of testing)

with gr.Blocks(css=css, analytics_enabled=False) as demo:
  gr.Markdown("# Student Notebook Thingy")
  with gr.Box():
    gr.HTML("""<span>Embed your OpenAI API key below; if you haven't created one already, visit
      <a href="https://platform.openai.com/account/api-keys">platform.openai.com/account/api-keys</a>
    to sign up for an account and get your personal API key</span>""",
            elem_classes="textbox_label")
    # TODO Find a better way to fix minor spacing issue below this element
    input = gr.Textbox(show_label=False, type="password", container=False,
                      placeholder="●●●●●●●●●●●●●●●●●")
    input.change(fn=embed_key, inputs=input, outputs=None)


  with gr.Blocks():
    gr.Markdown("## Add Document Source (File / Text / VectorStore)")
    # TODO Add entry for path to vector store (should be disabled for now)
    with gr.Row(equal_height=True):
      text_input = gr.TextArea(label='Copy and paste your text below',
                                lines=2)
      # TODO This is called every time the text changes, which is very
      # wasteful... the solution would be to only call this when necessary,
      # (i.e. when generating text), but that would require some extra
      # parameters passed in to the generating functions... maybe
      # add a check for that in the functions which reference the doc store?
      text_input.input(create_vector_store_from_text, [text_input], None)

      file_input = gr.Files(label="Load a .txt or .pdf file",
                            file_types=['.pdf', '.txt'], type="file",
                            elem_classes="short-height")
      file_input.change(create_vector_store_from_files, [file_input], None)

      text_input = gr.TextArea(label='Enter vector store URL, if given by instructor (WIP)',
                                lines=2, interactive=
                               False, elem_classes="translucent")

  with gr.Blocks():
    #gr.Markdown("## Optional: Enter Your Learning Objectives")
    learning_objectives = gr.Textbox(label='If provided by your instructor, please input your learning objectives for this session', value='')

  # Premade question prompts
  # TODO rename section?`
  with gr.Blocks():
    gr.Markdown("""
    ## Generate a Premade Prompt
    Select your type and number of desired questions. Click "Generate Prompt" to get your premade prompt,
    and then "Insert Prompt into Chat" to copy the text into the chat interface below. \
    You can also copy the prompt using the icon in the upper right corner and paste directly into the input box when interacting with the model.
    """)
    with gr.Row():
      with gr.Column():
        question_type = gr.Dropdown(["Multiple Choice", "True or False", "Short Answer", "Fill in the Blank", "Random"], label="Question Type")
        number_of_questions = gr.Textbox(label="Enter desired number of questions")
        sa_desired_length = gr.Dropdown(["1-2", "3-4", "5-6", "6 or more"], label = "For short answer questions only, choose the desired sentence length for answers. The default value is 1-2 sentences.")
      with gr.Column():
        prompt_button = gr.Button("Generate Prompt")
        premade_prompt_output = gr.Textbox(label="Generated prompt (save or copy)", show_copy_button=True)
        prompt_button.click(prompt_select,
                        inputs=[question_type, number_of_questions, sa_desired_length],
                        outputs=premade_prompt_output)

    insert_premade_prompt_button = gr.Button("Input Prompt into Chat")

  '''
  with gr.Blocks():
      # TODO Consider if we want to have this section
      # Maybe use this section for prompt refinement? E.g. you enter prompt
      # and model tells you how to improve it?
      gr.Markdown("""
      ## Write Your Own Custom Prompt
      For a comprehensive list of example prompts, see our repository's wiki: https://github.com/vanderbilt-data-science/lo-achievement/wiki/High-Impact-Prompts.
      After writing your prompt, be sure to click "Save Prompt" to save your prompt for chatting with the model below. You can also copy the prompt using the icon in the upper right corner and paste directly into the input box when interacting with the model.
      """)
      custom_prompt_block = gr.TextArea(label="Enter your own custom prompt", show_copy_button=True)
      #save_prompt_block = gr.Button("Save Prompt")
      #save_prompt_block.click(save_text, inputs=custom_prompt_block, outputs=None)
  '''

  # Chatbot (https://gradio.app/creating-a-chatbot/)
  '''
  with gr.Blocks():
    gr.Markdown("""
    ## Chat with the Model
    Click "Display Prompt" to display the premade or custom prompt that you created earlier. Then, continue chatting with the model.
    """)
    with gr.Row():
      show_prompt_block = gr.Button("Display Prompt")
  '''
  gr.Markdown("## Chat with the Model")
  with gr.Row(equal_height=True):
    with gr.Column(scale=2):
      chatbot = gr.Chatbot()
      with gr.Row():
        user_chat_input = gr.Textbox(label="User input", scale=9)
        user_chat_input.submit(return_text, inputs=None, outputs=user_chat_input)
        user_chat_submit = gr.Button("Ask/answer model", scale=1)
        #show_prompt_block.click(return_text, inputs=None, outputs=user_chat_input)

    # TODO Move the sources so it's displayed to the right of the chat bot,
    # with the sources taking up about 1/3rd of the horizontal space
    with gr.Box(elem_id="sources-container", scale=1):
      # TODO: Display document sources in a nicer format?
      gr.HTML(value="<h3 id='sources'>Sources</h3>")
      sources_output = []
      for i in range(num_sources):
        source_elem = gr.HTML(visible=False)
        sources_output.append(source_elem)

  # Copy text from premade prompt output to user chat input
  insert_premade_prompt_button.click(lambda text: text,
                        inputs=premade_prompt_output,
                        outputs=user_chat_input)

  # Display input and output in three-ish parts
  # (using asynchronous functions):
  # First show user input, then show model output when complete
  # Then wait until the bot provides response and return the result
  # Finally, allow the user to ask a new question by reenabling input
  async_response = user_chat_submit.click(user,
            [user_chat_input, chatbot],
            [user_chat_input, chatbot], queue=False) \
  .then(bot, chatbot, [chatbot, *sources_output], queue=True) \
  .then(reenable_chat, None, [user_chat_input], queue=False)

  with gr.Blocks():
    gr.Markdown("""
    ## Export Your Chat History
    Export your chat history as a .json, PDF file, .txt, or .csv file
    """)
    with gr.Row():
      export_dialogue_button = gr.Button("JSON")
      export_dialogue_button.click(save_chatbot_dialogue, chatbot, None)
      export_dialogue_button_pdf = gr.Button("PDF")
      export_dialogue_button_pdf.click(save_chatbot_dialogue_pdf, chatbot, None)
      export_dialogue_button_txt = gr.Button("TXT")
      export_dialogue_button_txt.click(save_as_txt, chatbot, None)
      export_dialogue_button_csv = gr.Button("CSV")
      export_dialogue_button_csv.click(save_as_csv, chatbot, None)

demo.queue()
#demo.launch(debug=True)
demo.launch()

<ipython-input-22-8f58a957929c>:113: GradioUnusedKwargWarning: You have unused kwarg parameters in Box, please remove them: {'scale': 1}
  with gr.Box(elem_id="sources-container", scale=1):


Setting queue=True in a Colab notebook requires sharing enabled. Setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Running on public URL: https://f880b30167f96bbba1.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
